In [21]:
import cupy as cp  # 替换 NumPy 为 CuPy
import numpy as np
import pandas as pd
from scipy import stats
from itertools import combinations
import matplotlib.pyplot as plt
from tqdm import tqdm
import os
import matplotlib.pyplot as plt
import networkx as nx

def calculate_ccg(reference_spikes, target_spikes, time_window=[-0.02, 0.02], 
                 bin_size=0.001, jitter_window=0.005, n_jitters=100, 
                 confidence_level=0.99):
    """优化后的 CCG 计算，完全在 GPU 上运行"""
    # 将数据移到 GPU
    ref_spikes = cp.sort(cp.asarray(reference_spikes))
    targ_spikes = cp.sort(cp.asarray(target_spikes))
    bins = cp.arange(time_window[0], time_window[1] + bin_size, bin_size)
    
    # 原始 CCG：向量化时间差计算
    time_diffs = targ_spikes[None, :] - ref_spikes[:, None]  # 广播生成时间差矩阵
    mask = (time_diffs >= time_window[0]) & (time_diffs <= time_window[1])
    time_diffs = time_diffs[mask]
    original_ccg, _ = cp.histogram(time_diffs, bins=bins)
    
    # 抖动计算（在 GPU 上）
    jittered_ccgs = cp.empty((n_jitters, len(bins) - 1), dtype=cp.int32)
    for i in range(n_jitters):
        jitter = cp.random.uniform(-jitter_window, jitter_window, size=len(targ_spikes))
        jittered_spikes = targ_spikes + jitter
        diffs = jittered_spikes[None, :] - ref_spikes[:, None]
        mask = (diffs >= time_window[0]) & (diffs <= time_window[1])
        ccg, _ = cp.histogram(diffs[mask], bins=bins)
        jittered_ccgs[i] = ccg
    
    # 统计计算（在 GPU 上）
    jitter_mean = cp.mean(jittered_ccgs, axis=0)
    jitter_std = cp.std(jittered_ccgs, axis=0, ddof=1)
    global_upper = cp.quantile(jittered_ccgs, confidence_level)
    global_lower = cp.quantile(jittered_ccgs, 1 - confidence_level)
    
    # 转换回 NumPy 以进行后续操作
    original_ccg = cp.asnumpy(original_ccg)
    jitter_mean = cp.asnumpy(jitter_mean)
    jitter_std = cp.asnumpy(jitter_std)
    global_upper = cp.asnumpy(global_upper)
    global_lower = cp.asnumpy(global_lower)
    bin_centers = cp.asnumpy((bins[:-1] + bins[1:]) / 2)
    
    analysis_range = (bin_centers >= 0.001) & (bin_centers <= 0.005)
    analysis_ccg = original_ccg[analysis_range]
    
    analysis_range_pre = (bin_centers >= -0.02) & (bin_centers < 0)
    analysis_ccg_pre= original_ccg[analysis_range_pre]
    peak_height_pre = np.max(analysis_ccg_pre)
    
    peak_height = np.max(analysis_ccg)
    trough_depth = np.min(analysis_ccg)
    peak_idx = np.argmax(analysis_ccg)
    trough_idx = np.argmin(analysis_ccg)
    full_indices = np.where(analysis_range)[0]
    
    peak_full_idx = full_indices[peak_idx]
    trough_full_idx = full_indices[trough_idx]
    strength = (peak_height - jitter_mean[peak_full_idx]) / jitter_std[peak_full_idx] \
        if peak_height > trough_depth else \
        (trough_depth - jitter_mean[trough_full_idx]) / jitter_std[trough_full_idx]
    
    connection_type = "none"
    if (peak_height > global_upper*1.2) & (peak_height_pre < global_upper):
        connection_type = "excitatory"
    elif trough_depth < global_lower:
        connection_type = "inhibitory"
    
    return {
        'original_ccg': original_ccg,
        'bin_centers': bin_centers,
        'connection_type': connection_type,
        'connection_strength': strength,
        'jitter_mean': jitter_mean,
        'global_upper': global_upper,
        'global_lower': global_lower
    }

def pair_analysis(pair, spike_times):
    ref_idx, targ_idx = pair
    return pair, calculate_ccg(spike_times[ref_idx], spike_times[targ_idx])

def plot_ccg(pair, results, save_path=None, bin_size=0.001):
    ref_idx, targ_idx = pair
    plt.figure(figsize=(10, 6))
    plt.bar(results['bin_centers'] * 1000, results['original_ccg'], 
            width=bin_size * 1000, color='blue', alpha=0.7, label='CCG')
    plt.plot(results['bin_centers'] * 1000, results['jitter_mean'], 'r--', label='Jitter Mean')
    plt.axhline(y=results['global_upper'], color='g', linestyle='--', label='Upper Threshold')
    plt.axhline(y=results['global_lower'], color='g', linestyle='--', label='Lower Threshold')
    plt.xlabel('Time Lag (ms)')
    plt.ylabel('Spike Count')
    plt.title(f'CCG: Neuron {ref_idx} → Neuron {targ_idx}\n'
              f'Type: {results["connection_type"]}, Strength: {results["connection_strength"]:.2f}')
    plt.axvline(0, color='k', linestyle='--', alpha=0.3)
    plt.legend()
    plt.grid(True, alpha=0.3)
    if save_path:
        plt.savefig(f"{save_path}/ccg_pair_{ref_idx}_{targ_idx}.png")
        plt.close()
    else:
        plt.show()

def analyze_all_pairs_from_df(df, spike_column='spike_times', plot=False, save_path=None, batch_size=3):
    """分块处理神经元对，显示已完成对数的进度条，并跳过 mean_firing_rate > 15 的参考神经元以及 target 为 'pyramidal' 的情况。
    在内存不足时跳过当前批次并继续处理。
    """
    # Check if required columns exist
    if 'cell_type' not in df.columns:
        raise ValueError("DataFrame must contain 'cell_type' column")
    if 'mean_firing_rate' not in df.columns:
        raise ValueError("DataFrame must contain 'mean_firing_rate' column")
    spike_times = {idx: np.asarray(row[spike_column]) if isinstance(row[spike_column], (list, np.ndarray)) 
                   else np.array([row[spike_column]]) 
                   for idx, row in df.iterrows()}
    
    if len(spike_times) < 2:
        raise ValueError("Need at least 2 neurons for pair analysis")
    
    # Get mean_firing_rate and cell_type
    mean_firing_rates = df['mean_firing_rate']
    cell_types = df['cell_type']
    
    # Generate pairs, filtering out mean_firing_rate > 15 for reference and 'pyramidal' for target
    pairs = []
    # for ref_idx, targ_idx in combinations(df.index, 2):
    #     if ((mean_firing_rates[ref_idx] <= 15) and 
    #         (cell_types[targ_idx] != 'pyramidal')):
    #         pairs.append((ref_idx, targ_idx))

    for ref_idx, targ_idx in combinations(df.index, 2):
        if (mean_firing_rates[ref_idx] <= 15) & (cell_types[ref_idx]=='pyramidal') & (cell_types[targ_idx]!='pyramidal'):
            pairs.append((ref_idx, targ_idx))

    total_pairs = len(pairs)
    if total_pairs == 0:
        print("No pairs to process after filtering (all reference neurons have mean_firing_rate > 15 or all targets are pyramidal).")
        return {}
    
    results_dict = {}
    completed_pairs = 0
    
    # Process pairs in batches with progress bar
    for i in tqdm(range(0, len(pairs), batch_size), 
                  total=(len(pairs) + batch_size - 1) // batch_size,
                  desc="Processing pairs"):
        batch_pairs = pairs[i:i + batch_size]
        try:
            batch_results = [pair_analysis(pair, spike_times) for pair in batch_pairs]
            results_dict.update(dict(batch_results))
            completed_pairs += len(batch_pairs)
            tqdm.write(f"Completed {completed_pairs}/{total_pairs} pairs")
        except cp.cuda.memory.OutOfMemoryError as e:
            tqdm.write(f"OutOfMemoryError: Skipping batch {i//batch_size + 1} due to {str(e)}. Continuing with next batch...")
            # Free up GPU memory explicitly if possible
            cp.get_default_memory_pool().free_all_blocks()
            continue  # Skip this batch and move to the next
    
    # Batch plotting
    if plot and save_path:
        if not os.path.exists(save_path):
            os.makedirs(save_path)
        for pair in tqdm(results_dict, desc="Plotting", total=len(results_dict)):
            plot_ccg(pair, results_dict[pair], save_path)
    
    return results_dict

def update_connectivity(df, results, spike_column='spike_times'):
    # Initialize 'connectivity' and 'connection_pairs' columns

    df['connectivity'] = [None] * len(df)
    df['connection_pairs'] = [[] for _ in range(len(df))]  # Initialize as empty lists for each neuron
    
    # Iterate through the results to update connectivity and connection pairs
    for pair, result in results.items():
        if result['connection_type'] == 'excitatory':  # Only consider excitatory connections
            ref_idx, targ_idx = pair
            
            # Update 'connectivity' column
            if pd.isnull(df.iloc[ref_idx]['connectivity']):
                df.iloc[ref_idx, df.columns.get_loc('connectivity')] = 'pre'
            if pd.isnull(df.iloc[targ_idx]['connectivity']):
                df.iloc[targ_idx, df.columns.get_loc('connectivity')] = 'post'

            # Update 'connection_pairs' column: append pair info
            df.iloc[ref_idx, df.columns.get_loc('connection_pairs')].append(f"{ref_idx}->{targ_idx}")
            #df.iloc[targ_idx, df.columns.get_loc('connection_pairs')].append(f"{ref_idx}->{targ_idx}")
    
    # # Convert empty lists to None or keep as lists, depending on preference
    # df['connection_pairs'] = df['connection_pairs'].apply(lambda x: x if x else None)
    
    return df


import matplotlib.pyplot as plt
import numpy as np

def plot_ccg_of_pairs(df, save_path=None, bin_size=0.001, figsize=(10, 6), 
                     time_window=[-0.02, 0.02], jitter_window=0.005, n_jitters=10, 
                     confidence_level=0.99,spike_column="spike_times", pre_fix=None):
    """
    Plot CCGs for all excitatory connection pairs identified in the DataFrame, 
    recalculating CCGs from spike times.
    
    Parameters:
    - df: DataFrame with 'connection_pairs' and 'spike_times' columns
    - save_path: Optional directory to save the plots (e.g., 'path/to/save/')
    - bin_size: Bin size for CCG histogram
    - figsize: Tuple for figure size (width, height)
    - time_window, jitter_window, n_jitters, confidence_level: Parameters for calculate_ccg
    """
    # Ensure save_path exists if provided
    if save_path and not os.path.exists(save_path):
        os.makedirs(save_path)
    
    # Check required columns
    if 'connection_pairs' not in df.columns or 'spike_times' not in df.columns:
        raise ValueError("DataFrame must contain 'connection_pairs' and 'spike_times' columns")
    
    # Extract spike times
    spike_times = {idx: np.asarray(row[spike_column]) if isinstance(row[spike_column], (list, np.ndarray)) 
                   else np.array([row[spike_column]]) 
                   for idx, row in df.iterrows()}
    
    
    # Collect all unique pairs from 'connection_pairs'
    plotted_pairs = set()
    for idx, row in df.iterrows():
        for idx, row in df.iterrows():
            if (row['connection_pairs'] and 
                not isinstance(row['connection_pairs'], list) and 
                row['connection_pairs'] is not None):  # Check if there are any pairs
                try:
                    ref_idx, targ_idx = map(int, row['connection_pairs'].split('->'))
                    pair = (ref_idx, targ_idx)
                    print(pair)
                              
                    if pair not in plotted_pairs:

                        plotted_pairs.add(pair)
                        
                        # Recalculate CCG for this pair
                        result = calculate_ccg(spike_times[ref_idx], spike_times[targ_idx],
                                            time_window=time_window, bin_size=bin_size,
                                            jitter_window=jitter_window, n_jitters=n_jitters,
                                            confidence_level=confidence_level)
                        
                        # Plot the CCG
                        if result['connection_type'] is not None:
                            plt.figure(figsize=figsize)
                            plt.bar(result['bin_centers'] * 1000, result['original_ccg'], 
                                    width=bin_size * 1000, color='blue', alpha=0.7, label='CCG')
                            plt.plot(result['bin_centers'] * 1000, result['jitter_mean'], 
                                    'r--', label='Jitter Mean')
                            plt.axhline(y=result['global_upper'], color='g', linestyle='--', 
                                    label='Upper Threshold')
                            plt.axhline(y=result['global_lower'], color='g', linestyle='--', 
                                    label='Lower Threshold')
                            plt.xlabel('Time Lag (ms)')
                            plt.ylabel('Spike Count')
                            cell1 = df['cell_type'].iloc[ref_idx]
                            cell2 = df['cell_type'].iloc[targ_idx]
                            
                            plt.title(f'CCG: Neuron {ref_idx} → Neuron {targ_idx}\n'
                                    f'Type: {result["connection_type"]}, '
                                    f'Strength: {result["connection_strength"]:.2f}'
                                    f'cell type: ref:{cell1}, target:{cell2}')
                            plt.axvline(0, color='k', linestyle='--', alpha=0.3)
                            plt.legend()
                            plt.grid(True, alpha=0.3)
                            
                            # Save or show the plot
                            if save_path:
                                plt.savefig(f"{save_path}/{pre_fix}_{ref_idx}_{targ_idx}.png",
                                        bbox_inches='tight', dpi=300)
                                plt.close()
                            else:
                                plt.show()
                except ValueError:
                    print(f"Skipping invalid pair format: {row['connection_pairs']}")

                    continue
            elif isinstance(row['connection_pairs'], list) and row['connection_pairs']:
                    
                    for pair_str in row['connection_pairs']:
                        ref_idx, targ_idx = map(int, pair_str.split('->'))
                        pair = (ref_idx, targ_idx)
                        print(pair)
                              
                        if pair not in plotted_pairs:

                            plotted_pairs.add(pair)
                            
                            # Recalculate CCG for this pair
                            result = calculate_ccg(spike_times[ref_idx], spike_times[targ_idx],
                                                time_window=time_window, bin_size=bin_size,
                                                jitter_window=jitter_window, n_jitters=n_jitters,
                                                confidence_level=confidence_level)
                            
                            # Plot the CCG
                            if result['connection_type'] is not None:
                                plt.figure(figsize=figsize)
                                plt.bar(result['bin_centers'] * 1000, result['original_ccg'], 
                                        width=bin_size * 1000, color='blue', alpha=0.7, label='CCG')
                                plt.plot(result['bin_centers'] * 1000, result['jitter_mean'], 
                                        'r--', label='Jitter Mean')
                                plt.axhline(y=result['global_upper'], color='g', linestyle='--', 
                                        label='Upper Threshold')
                                plt.axhline(y=result['global_lower'], color='g', linestyle='--', 
                                        label='Lower Threshold')
                                plt.xlabel('Time Lag (ms)')
                                plt.ylabel('Spike Count')
                                plt.title(f'CCG: Neuron {ref_idx} → Neuron {targ_idx}\n'
                                        f'Type: {result["connection_type"]}, '
                                        f'Strength: {result["connection_strength"]:.2f}'
                                        f'cell type: ref:{cell1}, target:{cell2}')
                                plt.axvline(0, color='k', linestyle='--', alpha=0.3)
                                plt.legend()
                                plt.grid(True, alpha=0.3)
                                
                                # Save or show the plot
                                if save_path:
                                    plt.savefig(f"{save_path}/{pre_fix}_{ref_idx}_{targ_idx}.png",
                                            bbox_inches='tight', dpi=300)
                                    plt.close()
                                else:
                                    plt.show()


In [24]:
def get_pkl_files(folder_path):
    # List all files in the directory
    all_files = os.listdir(folder_path)
    # Filter files that end with "withDLC.pkl"
    pkl_files = [f for f in all_files if f.endswith("withDLC.pkl")]
    return pkl_files

# Example usage
#folder_path = r"S:\Sachuriga\filre_with_table\adjust_y_with _meanVAlue\clusters_with_tsneLabel\ripple_max"  # Replace with your actual folder path
adjust_path = r"S:\Sachuriga\file_with_table\ripple_ch"
out_path = r"S:\Sachuriga\file_with_table\ripple_ch/Functional_connections"
new_files = []
pkl_files = get_pkl_files(adjust_path)
erro_log=[]
for file in pkl_files:
#file=pkl_files[0]
    df_loaded = pd.read_pickle(fr'{adjust_path}/{file}').reset_index(drop=True)

    uniques = np.unique(df_loaded['session_id'])
    new_df = []
    for u in uniques:
        results = []
        temp = df_loaded[df_loaded['session_id']==u].copy()
        

        df_loaded['connectivity'] = None
        df_loaded['connection_pairs'] = None
        
        df_loaded[df_loaded['session_id']==u]['connectivity'] = [None] * len(df_loaded[df_loaded['session_id']==u])
        df_loaded[df_loaded['session_id']==u]['connection_pairs'] = [[] for _ in range(len(df_loaded[df_loaded['session_id']==u]))]  # Initialize as empty lists for each neuron

        try:
            results = analyze_all_pairs_from_df(temp, plot=False) 
                        # Iterate through the results to update connectivity and connection pairs
            for pair, result in results.items():
                if result['connection_type'] == 'excitatory':  # Only consider excitatory connections
                    ref_idx, targ_idx = pair
                    # Use .loc with the actual index values from the filtered DataFrame
                    df_loaded.iloc[ref_idx, df_loaded.columns.get_loc('connectivity')] = 'pre'
                    df_loaded.iloc[targ_idx, df_loaded.columns.get_loc('connectivity')] = 'post'

                    # Update 'connection_pairs' column: append pair info
                    df_loaded.iloc[ref_idx, df_loaded.columns.get_loc('connection_pairs')] = f"{ref_idx}->{targ_idx}"
        except Exception as e:
            erro_log.append((file,e))
    
    if os.path.exists(fr"{out_path}/{file}"):
        os.remove(fr"{out_path}/{file}")
    df_loaded.to_pickle(fr"{out_path}/{file}")


Processing pairs:   2%|▏         | 1/46 [00:00<00:26,  1.71it/s]

Completed 3/137 pairs


Processing pairs:   4%|▍         | 2/46 [00:01<00:21,  2.05it/s]

Completed 6/137 pairs


Processing pairs:   7%|▋         | 3/46 [00:01<00:15,  2.78it/s]

...

OutOfMemoryError: Skipping batch 21 due to Out of memory allocating 35,571,218,432 bytes (allocated so far: 49,826,217,984 bytes).. Continuing with next batch...


Processing pairs:  96%|█████████▌| 22/23 [28:18<03:40, 220.11s/it]

Completed 63/67 pairs


Processing pairs: 100%|██████████| 23/23 [28:48<00:00, 75.15s/it] 


OutOfMemoryError: Skipping batch 23 due to Out of memory allocating 24,599,816,704 bytes (allocated so far: 69,979,632,128 bytes).. Continuing with next batch...


In [23]:
file=r"63383_2024-07-10_15-37-51_units_table_withDLC.pkl"
df_loaded=pd.read_pickle(fr"S:\Sachuriga\file_with_table\ripple_ch\Functional_connections/{file}")
plot_ccg_of_pairs(df_loaded, save_path=fr'Q:\sachuriga\CR_CA1_paper\Results\connectivity', pre_fix = file.split("units_table_withDLC.pkl")[0])

(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8,

In [17]:
df_loaded

level_0  index                                        spike_times  \
0         0      0  [79.80586666666666, 82.36903333333333, 82.5270...   
1         1      1  [355.5495666666667, 494.1717, 555.7439, 658.68...   
2         2     14  [82.09543333333333, 136.72986666666668, 136.74...   
3         3     15  [64.0384, 64.07413333333334, 64.1816, 64.1974,...   
4         0      2  [85.13216666666666, 85.2458, 85.54376666666667...   
5         1     16  [64.0338, 64.04926666666667, 64.14776666666667...   
6         2     17  [76.90883333333333, 84.95836666666666, 88.5522...   
7         3     18  [69.25403333333334, 69.27493333333334, 69.4856...   
8         0      3  [64.58993333333333, 64.67256666666667, 64.6925...   
9         1      4  [80.59643333333334, 80.6237, 80.6897, 80.7649,...   
10        2     19  [64.04016666666666, 64.07173333333333, 64.0957...   
11        3     20  [64.37293333333334, 64.4798, 64.49963333333334...   
12        0      5  [67.74913333333333, 67.75976666666666, 67.7682...   
13        1      6  [137.47613333333334, 137.48726666666667, 137.5...   
14        2      7  [69.92313333333334, 118.98126666666667, 119.32...   
15        3      8  [119.7886, 119.7949, 119.79836666666667, 119.8...   
16        4     21  [64.02343333333333, 64.0361, 64.04443333333333...   
17        5     22  [64.60126666666666, 65.1374, 65.16613333333333...   
18        6     23  [64.07293333333334, 64.1894, 64.47903333333333...   
19        7     24  [64.0808, 64.29566666666666, 64.30173333333333...   
20        8     25  [85.21646666666666, 85.23886666666667, 85.2586...   
21        0      9  [65.16173333333333, 65.6292, 65.65236666666667...   
22        1     10  [64.39616666666667, 64.45976666666667, 65.0193...   
23        2     11  [67.0806, 69.38883333333334, 69.96626666666667...   
24        3     12  [94.18466666666667, 115.74523333333333, 118.96...   
25        4     26  [66.1892, 66.7591, 66.7661, 66.7791, 66.8539, ...   
26        5     27  [84.32256666666666, 89.024, 91.43116666666667,...   
27        0     13  [67.61136666666667, 69.1128, 69.36873333333334...   
28        1     28  [64.02663333333334, 64.04326666666667, 64.1772...   
29        2     29  [64.0335, 64.03673333333333, 64.12843333333333...   
30        3     30  [64.0739, 64.34473333333334, 64.3565, 64.38816...   
31        4     31  [71.73523333333333, 72.09286666666667, 73.9213...   
32        5     32  [64.04396666666666, 64.05713333333334, 64.1189...   

   unit_name  sd_ratio  sync_spike_8.1  presence_ratio  cluster_id.30  \
0          5  1.911421             0.0        1.000000            0.0   
1          6  2.804665             0.0        0.473684            1.0   
2         54  1.646448             0.0        0.894737           14.0   
3          3  1.228305             0.0        1.000000           17.0   
4         14  2.514760             0.0        1.000000            2.0   
5          8  1.030076             0.0        1.000000           19.0   
6          9  1.285850             0.0        1.000000           20.0   
7         13  1.368713             0.0        1.000000           21.0   
8         17  1.383377             0.0        1.000000            3.0   
9         20  1.409312             0.0        1.000000            4.0   
10        18  1.158261             0.0        1.000000           22.0   
11        19  1.166965             0.0        1.000000           23.0   
12        25  1.292258             0.0        1.000000            5.0   
13        26  1.598365             0.0        0.947368            6.0   
14        27  1.581420             0.0        0.947368            7.0   
15        28  1.921309             0.0        1.000000            8.0   
16        23  1.068981             0.0        1.000000           24.0   
17        24  1.030273             0.0        1.000000           25.0   
18        30  1.150234             0.0        1.000000           26.0   
19        31  1.953615             0.0        0.947368       

In [25]:
import pandas as pd
def get_pkl_files(folder_path):
    # List all files in the directory
    all_files = os.listdir(folder_path)
    # Filter files that end with "withDLC.pkl"
    pkl_files = [f for f in all_files if f.endswith("withDLC.pkl")]
    return pkl_files

# Example usage
#folder_path = r"S:\Sachuriga\filre_with_table\adjust_y_with _meanVAlue\clusters_with_tsneLabel\ripple_max"  # Replace with your actual folder path
adjust_path = r"S:\Sachuriga\file_with_table\ripple_ch\Functional_connections"
new_files = []
pkl_files = get_pkl_files(adjust_path)
erro_log=[]
for file in pkl_files:
    df_loaded = pd.read_pickle(fr"{adjust_path}/{file}")
    try:
        plot_ccg_of_pairs(df_loaded, save_path=fr'Q:\sachuriga\CR_CA1_paper\Results\connectivity',pre_fix = file.split("units_table_withDLC.pkl")[0])
    except Exception as e:
        continue

(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8, 10)
(22, 32)
(24, 28)
(0, 3)
(8,

In [ ]:
import pandas as pd
def get_pkl_files(folder_path):
    # List all files in the directory
    all_files = os.listdir(folder_path)
    # Filter files that end with "withDLC.pkl"
    pkl_files = [f for f in all_files if f.endswith("withDLC.pkl")]
    return pkl_files

# Example usage
#folder_path = r"S:\Sachuriga\filre_with_table\adjust_y_with _meanVAlue\clusters_with_tsneLabel\ripple_max"  # Replace with your actual folder path
adjust_path = r"S:\Sachuriga\filre_with_table\adjust_y_with _meanVAlue\clusters_with_tsneLabel\ripple_max\ripple_py"
new_files = []
pkl_files = get_pkl_files(adjust_path)
erro_log=[]
for file in pkl_files:
    df_loaded = pd.read_pickle(fr"{adjust_path}/{file}")

In [4]:
import pandas as pd

temp = pd.read_pickle(r"S:\Sachuriga\filre_with_table\adjust_y_with _meanVAlue\clusters_with_tsneLabel\ripple_max\ripple_py/63383_2024-07-10_A_units_table_withDLC.pkl")
temp

level_0  index                                        spike_times  \
0         0      0  [79.80586666666666, 82.36903333333333, 82.5270...   
1         1      1  [355.5495666666667, 494.1717, 555.7439, 658.68...   
2         2      2  [82.09543333333333, 136.72986666666668, 136.74...   
3         3      5  [64.0384, 64.07413333333334, 64.1816, 64.1974,...   
4         4      0  [85.13216666666666, 85.2458, 85.54376666666667...   
5         5      1  [64.0338, 64.04926666666667, 64.14776666666667...   
6         6      2  [76.90883333333333, 84.95836666666666, 88.5522...   
7         7      3  [69.25403333333334, 69.27493333333334, 69.4856...   
8         8      0  [64.58993333333333, 64.67256666666667, 64.6925...   
9         9      1  [80.59643333333334, 80.6237, 80.6897, 80.7649,...   
10       10      2  [64.04016666666666, 64.07173333333333, 64.0957...   
11       11      3  [64.37293333333334, 64.4798, 64.49963333333334...   
12       12      0  [67.74913333333333, 67.75976666666666, 67.7682...   
13       13      1  [137.47613333333334, 137.48726666666667, 137.5...   
14       14      2  [69.92313333333334, 118.98126666666667, 119.32...   
15       15      3  [119.7886, 119.7949, 119.79836666666667, 119.8...   
16       16      4  [64.02343333333333, 64.0361, 64.04443333333333...   
17       17      5  [64.60126666666666, 65.1374, 65.16613333333333...   
18       18      6  [64.07293333333334, 64.1894, 64.47903333333333...   
19       19      7  [64.0808, 64.29566666666666, 64.30173333333333...   
20       20      8  [85.21646666666666, 85.23886666666667, 85.2586...   
21       21      0  [65.16173333333333, 65.6292, 65.65236666666667...   
22       22      1  [64.39616666666667, 64.45976666666667, 65.0193...   
23       23      2  [67.0806, 69.38883333333334, 69.96626666666667...   
24       24      3  [94.18466666666667, 115.74523333333333, 118.96...   
25       25      4  [66.1892, 66.7591, 66.7661, 66.7791, 66.8539, ...   
26       26      5  [84.32256666666666, 89.024, 91.43116666666667,...   
27       27      0  [67.61136666666667, 69.1128, 69.36873333333334...   
28       28      1  [64.02663333333334, 64.04326666666667, 64.1772...   
29       29      2  [64.0335, 64.03673333333333, 64.12843333333333...   
30       30      3  [64.0739, 64.34473333333334, 64.3565, 64.38816...   
31       31      4  [71.73523333333333, 72.09286666666667, 73.9213...   
32       32      5  [64.04396666666666, 64.05713333333334, 64.1189...   

   unit_name  nn_miss_rate  num_negative_peaks.1  recovery_slope  \
0          5      0.009684                   1.0  -135826.081350   
1          6      0.000857                   1.0  -189691.323121   
2         54      0.017727                   1.0   -78118.659925   
3          3      0.051157                   1.0   -84398.764292   
4         14      0.000667                   1.0  -130640.317634   
5          8      0.043691                   1.0   -41703.661563   
6          9      0.012146                   1.0  -108480.483263   
7         13      0.024629                   1.0  -102456.294835   
8         17      0.002000                   1.0   -43784.124843   
9         20      0.009000                   1.0  -114143.425971   
10        18      0.002833                   1.0  -101396.674573   
11        19      0.015500                   1.0   -64344.172966   
12        25      0.003367                   1.0  -140717.915608   
13        26      0.007417                   1.0   -79880.002512   
14        27      0.001658                   1.0  -141262.748450   
15        28      0.002162                   1.0  -106073.755624   
16        23      0.003939                   1.0   -76967.747299   
17        24      0.009886                   1.0   -60810.170588   
18        30      0.005792                   1.0   -61397.657052   
19        31      0.003244                   1.0  -143401.404331   
20        32      0.002952                   1.0  -100188.110058   
21        38      0.00482

In [45]:
df_loaded = pd.read_pickle(r'Q:/sachuriga/CR_CA1_paper/tables/functional_properties_with_python_measurements.pkl')
df_loaded 

spike_times unit_name  sd_ratio  \
0     [79.80586666666666, 82.36903333333333, 82.5270...         5  1.911421   
1     [355.5495666666667, 494.1717, 555.7439, 658.68...         6  2.804665   
2     [85.13216666666666, 85.2458, 85.54376666666667...        14  2.514760   
3     [64.58993333333333, 64.67256666666667, 64.6925...        17  1.383377   
4     [80.59643333333334, 80.6237, 80.6897, 80.7649,...        20  1.409312   
...                                                 ...       ...       ...   
1632  [49.6793, 49.982733333333336, 59.4068, 59.9050...        57  1.099195   
1633  [53.8643, 53.8726, 54.225033333333336, 54.2430...        58  1.326882   
1634  [53.4344, 53.44533333333333, 81.99256666666666...        59  1.192254   
1635  [49.797266666666665, 49.8036, 49.8072666666666...        64  1.134203   
1636  [57.445566666666664, 61.043933333333335, 105.3...        65  2.047484   

      sync_spike_8.1  presence_ratio  cluster_id.30  half_width     l_ratio.1  \
0                0.0        1.000000            0.0    0.000113  5.665784e-03   
1                0.0        0.473684            1.0    0.000097  8.633910e-10   
2                0.0        1.000000            2.0    0.000143  2.147104e-05   
3                0.0        1.000000            3.0    0.000177  7.603359e-10   
4                0.0        1.000000            4.0    0.000150  9.093921e-04   
...              ...             ...            ...         ...           ...   
1632             0.0        0.951220           37.0    0.000193  2.283637e-04   
1633             0.0        1.000000           38.0    0.000103  9.846390e-11   
1634             0.0        1.000000           39.0    0.000113  3.331845e-10   
1635             0.0        1.000000           40.0    0.000080  6.495784e-13   
1636             0.0        0.853659           41.0    0.000133  1.070938e-11   

      recovery_slope.1  cluster_id.19  ...  \
0       -135826.081350            0.0  ...   
1       -189691.323121            1.0  ...   
2       -130640.317634            2.0  ...   
3        -43784.124843            3.0  ...   
4       -114143.425971            4.0  ...   
...                ...            ...  ...   
1632    -135012.562402           37.0  ...   
1633    -151900.470747           38.0  ...   
1634    -110412.581312           39.0  ...   
1635     -58727.597060           40.0  ...   
1636    -156831.938611           41.0  ...   

                               Information_rate_shuffle  \
0     [0.08267061469140277, 0.07041850473158107, 0.0...   
1     [0.0046000656646308, 0.006003005776661359, 0.0...   
2     [0.16682928755903226, 0.16373066455687435, 0.1...   
3     [0.27578301075317646, 0.3321477947339928, 0.23...   
4     [0.2578941305273307, 0.32478360753427016, 0.24...   
...                                                 ...   
1632  [0.18070849497114827, 0.19216866085275203, 0.1...   
1633  [0.3131061792454255, 0.3433444304773335, 0.310...   
1634  [0.1425076671837233, 0.14337168470165845, 0.14...   
1635  [0.10621767214329197, 0.08078383258382504, 0.1...   
1636  [0.1284939470839548, 0.10619117775362028, 0.09...   

                       Information_content_rate_shuffle  \
0     [1.047799597257073, 1.111370079574923, 1.00055...   
1     [2.999704145684937, 3.7992320302401033, 4.2622...   
2     [0.8870832166369713, 0.8437193385756397, 0.824...   
3     [0.4707288740300241, 0.36624365369205025, 0.45...   
4     [0.950750862993962, 0.7775513219939735, 0.5841...   
...                                                 ...   
1632  [0.8566544839668675, 0.8463012846604321, 0.897...   
1633  [0.24469560665882778, 0.32463472308943747, 0.2...   
1634  [0.4251077208323871, 0.25045816544868793, 0.33...   
1635  [0.30992199961925043, 0.4732354679856963, 0.28...   
1636  [0.6606264244266672, 0.9619299782986793, 0.821...   

                                       Sparsity_shuffle  \
0     [0.32908149768123185, 0.39234477721758776, 0.4...   
1     [0.10204609903178616, 0.053